# CASFM Uncertainty Vizualizations - Lower Fourmile

In [1]:
import pandas as pd
import numpy as np
import scipy.special
from sklearn.preprocessing import normalize
from sklearn import preprocessing

# Import figure from bokeh.plotting
from bokeh.io import show, output_notebook, output_file
from bokeh.plotting import figure
from bokeh.models import LinearAxis, Range1d

## Import results data

In [63]:
# Read in the CSV file: df
df = pd.read_csv('results_q.csv', header=None)

# Correct header to show average discharge
# iterate over relevant rows
i = 4

# iterate over relevant columns
for j in range(10,510):
    # append average discharge of reach, after converting to 1 decimal
    cfs_float = float(df.iloc[0,j])
    df.iloc[i,j]= np.round(cfs_float,decimals=0)
    
# Append statistic columns and average discharges to column names
for j in range(0,510):
    df.rename(columns={j:df.iloc[i,j]}, inplace=True)

# drop the first 4 rows, drop columns with all NaN values
df = df.iloc[5:]
df = df.dropna(axis=1, how='all')

# rearrange the dataframe with q values ascending, statistic columns in place
stats_columns = list(df.columns.values[0:10])
value_columns = list(df.columns.values[10:])
value_columns = sorted(value_columns)
reorder_columns = stats_columns + value_columns
df = df[reorder_columns]

df

XS   DIFF      MAX     AVERAGE      MIN  STDEV   99th PCT  \
5    24915.69  13.73  6603.74   6598.5025  6590.01  2.043  6602.5205   
6    24750.84   6.79  6591.74   6588.7855  6584.95  1.206  6590.9004   
7    24494.04   7.21  6581.11  6578.14286   6573.9  1.209  6580.3306   
8    24361.28   5.82  6570.15  6567.78162  6564.33  0.992  6569.4404   
9    24241.61   5.55  6562.44  6559.81938  6556.89  0.903  6561.5708   
10   24084.46   7.69  6556.88  6553.15896  6549.19  1.301  6555.6014   
11   23948.67   9.46  6551.48  6546.88774  6542.02  1.613  6549.9714   
12   23791.52   8.84  6540.27   6536.0081  6531.43  1.476  6538.8512   
13   23592.79   8.03  6530.05  6526.47352  6522.02  1.399  6528.9308   
14   23394.54   9.29  6521.96  6517.61538  6512.67  1.639   6520.691   
15   23237.74  10.01  6513.05  6507.84344  6503.04  1.484    6510.48   
16    23135.2   6.43  6505.52  6502.88472  6499.09  0.933  6504.6109   
17   22973.63   6.33  6500.29   6497.6936  6493.96  0.929  6499.4001   
18   22797.07   10.1  6496.02   6491.1541  6485.92  1.709  6494.4309   
19   22586.27   5.81  6485.16   6482.5909  6479.35  0.889  6484.2908   
20   22472.58   8.35  6482.31   6478.5012  6473.96  1.378  6480.7015   
21   22435.48   9.14  6480.46  6476.84372  6471.32  1.891  6479.5508   
22   22290.02  12.79  6478.76  6473.11478  6465.97  2.818  6477.1011   
23   22238.77  10.41  6475.68  6471.91702  6465.27  2.932  6475.4505   
24      22227    NaN      NaN         NaN      NaN    NaN        NaN   
25   22214.08   8.42  6471.56  6467.85746  6463.14  1.363  6470.3408   
26   22145.46  11.28  6470.11  6464.04902  6458.83  1.761    6468.28   
27   22036.57   9.19   6463.5  6459.37988  6454.31  1.308  6461.7311   
28   21860.42   7.59  6453.34  6450.30854  6445.75  1.294    6452.36   
29   21713.12   8.37  6449.84  6446.90146  6441.47  1.505  6449.0706   
30   21607.41   7.94  6446.04  6442.80422   6438.1  1.461  6445.1108   
31   21528.62   8.73  6444.24  6439.92818  6435.51   1.17  6442.3516   
32   21465.59   8.46   6441.6  6437.62334  6433.14  1.387  6440.2911   
33   21352.49  12.05  6440.28  6434.04734  6428.23  1.953  6439.0516   
34   21182.64   8.28  6426.88  6422.72356   6418.6  1.416   6425.531   
..        ...    ...      ...         ...      ...    ...        ...   
204  2250.823   9.67  5784.24  5780.49898  5774.57  1.143  5783.0023   
205  2213.814  10.75  5784.25  5779.80296   5773.5  1.322  5782.9118   
206  2075.393  14.71  5784.57  5779.84662  5769.86  1.919  5783.3417   
207  2018.982  14.16  5783.52  5779.06018  5769.36  1.894  5782.4016   
208      2000    NaN      NaN         NaN      NaN    NaN        NaN   
209  1967.518  11.64   5778.8   5775.5366  5767.16  1.925  5778.0711   
210  1881.535  12.85  5777.85   5773.9916     5765  2.244  5776.9512   
211  1760.866  15.61  5777.71  5773.54884   5762.1  2.821  5776.7713   
212      1750    NaN      NaN         NaN      NaN    NaN        NaN   
213  1733.456  12.55  5774.31  5769.05052  5761.76  2.076  5773.5013   
214  1698.578  11.09  5771.81   5767.7947  5760.72  1.568  5770.8815   
215  1632.338  11.16  5770.63  5767.26286  5759.47  1.223  5769.7605   
216      1615    NaN      NaN         NaN      NaN    NaN        NaN   
217  1598.605   9.64  5768.37  5765.25826  5758.73  1.346   5767.561   
218  1472.576  11.19  5765.79  5762.49152   5754.6  1.762  5765.2402   
219  1412.559  13.42  5765.88   5762.2358  5752.46  2.153  5765.2803   
220      1400    NaN      NaN         NaN      NaN    NaN        NaN   
221  1386.148  11.43  5763.48   5760.1831  5752.05  2.005  5762.8708   
222  1288.404  10.68  5761.46  5758.12846  5750.78  1.801     5760.6   
223  1114.442  10.82     5758  5754.69948  5747.18  1.763  5757.3409   
224  904.2737   9.35  5753.53  5750.58988  5744.18  1.158   5752.711   
225  835.5021   9.95  5753.38  5750.43238  5743.43  1.186   5752.551   
226       820    NaN      NaN         NaN      NaN    NaN        NaN   
227  808.9484  10.19  5750.48  5747.48342  5740.29 

## Import profile data

In [3]:
df_profile = pd.read_csv('Profile.csv')
df_profile.head()

Line Style  \
0        Label   
1            x   
2  32.19000244   
3  32.19000244   
4  82.19000244   

  Variable=Deck, Line Style=1, Line Color=1, Line Width=0, Sym Type=0, Sym Color=0, Sym Size=0, Polygon=-1, FillMode=1, FillColor=12632256, On Bottom(in legend)=False, Sort (in legend)=0, Legend Only=0  \
0                                                NaN                                                                                                                                                        
1                                                  y                                                                                                                                                        
2                                        5717.399902                                                                                                                                                        
3                                        5739.055176                                                                                                                                                        
4                                        5742.049805                                                                                                                                                        

  Line Style.1  \
0        Label   
1            x   
2          NaN   
3          NaN   
4          NaN   

  Variable=Lateral Structure, Line Style=1, Line Color=1, Line Width=0, Sym Type=0, Sym Color=0, Sym Size=0, Polygon=-1, FillMode=1, FillColor=12632256, On Bottom(in legend)=False, Sort (in legend)=0, Legend Only=0  \
0                                         Lat Struct                                                                                                                                                                     
1                                                  y                                                                                                                                                                     
2                                                NaN                                                                                                                                                                     
3                                                NaN                                                                                                                                                                     
4                                                NaN                                                                                                                                                                     

  Line Style.2  \
0        Label   
1            x   
2  23.19000244   
3  23.19000244   
4  93.19000244   

  Variable=Culvert, Line Style=1, Line Color=1, Line Width=0, Sym Type=0, Sym Color=0, Sym Size=0, Polygon=-1, FillMode=1, FillColor=16777215, On Bottom(in legend)=False, Sort (in legend)=0, Legend Only=0  \
0                                                NaN                                                                                                                                                           
1                                                  y                                                                                                                                                           
2                                               5719                                                                                                                                                           
3                                               5733                                                                                                                                                           
4                                               5734                                             

In [4]:
# df_profile_cols = df_profile.columns.values

# for j in range(len(df_profile_cols)):
#     label1 = df_profile[df_profile.columns[j]].iloc[0]
#     label2 = df_profile_cols[j]
#     label3 = label2 + '_' + label1
#     # Append x,y labels to existing columns headers
#     df_profile.rename(columns={label2:label3}, inplace=True)  

# # Drop the first row now that its appended to the column headers
# # df_profile = df_profile.iloc[1:,:]

# # Convert to numeric from string
# # df_profile[['Label.1_x', 'Ground_y']] = df_profile[['Label.1_x','Ground_y']].apply(pd.to_numeric)

# df_profile.head()

## Define percentiles - q

In [5]:
# Define the percentile ranges of interest
q_percentiles = [10,25,75,90]
q_vals = (df.columns.values[10:])
q_percentile_vals = np.percentile(q_vals, q_percentiles)
q_percentile_vals

# Find the median of the q values

# If dataset is even in length, drop the last entry to avoid averaging middle two values
if np.remainder(len(q_vals), 2) == 0:
    q_vals_even = q_vals[:-1]
    q_median = np.median(q_vals_even)
else:
    q_median = np.median(q_vals)

# q_median = np.median(q_vals)
print ('median of q_vals: ', q_median)

median of q_vals:  3757.0


## Define colors for plots

In [6]:
# For 4 breaks (5 bins) in the percentiles plus 1 extra for median water surface
# colors = ['red', 'orange', 'blue', 'orange', 'red', 'yellow'] # primaries
# colors = ['blue', 'blue', 'blue', 'blue', 'blue', 'blue'] # monotone blues
# colors = ['#F751DB','#DBF751', '#51DBF7', '#DBF751', '#F751DB', '#5163F7'] # florescents
colors = ['#DC11D7', '#7C11DC' ,'#1611DC', '#7C11DC', '#DC11D7', '#11DCD4']

## Import profile ground data

In [7]:
# Import xs data from hec-ras' profile plot, copy values to clipboard option
df_profile = pd.read_csv('Profile.csv', header=1)

df_profile_cols = df_profile.columns.values

for j in range(len(df_profile_cols)):
    label1 = df_profile[df_profile.columns[j]].iloc[0]
    label2 = df_profile_cols[j]
    label3 = label2 + '_' + label1

    # Append x,y labels to existing columns headers
    df_profile.rename(columns={label2:label3}, inplace=True)  

# Drop the first row now that its appended to the column headers
df_profile = df_profile.iloc[1:,:]

df_profile_cols = df_profile.columns.values
print(df_profile_cols)

# Convert to numeric from string
df_profile[['Label.8_x', 'Ground_y']] = df_profile[['Label.8_x','Ground_y']].apply(pd.to_numeric)

df_profile.head()

['Label_x' 'Unnamed: 1_y' 'Label.1_x' 'Lat Struct_y' 'Label.2_x'
 'Unnamed: 5_y' 'Label.3_x' 'Unnamed: 7_y' 'Label.4_x' 'Unnamed: 9_y'
 'Label.5_x' 'Unnamed: 11_y' 'Label.6_x' 'Unnamed: 13_y' 'Label.7_x'
 'Unnamed: 15_y' 'Label.8_x' 'Ground_y' 'Label.9_x' 'Unnamed: 19_y'
 'Label.10_x' 'Left Levee_y' 'Label.11_x' 'Right Levee_y' 'Label.12_x'
 'WS  CWCB-100yr_y' 'Label.13_x' 'Set WS_y']


Label_x Unnamed: 1_y Label.1_x Lat Struct_y    Label.2_x Unnamed: 5_y  \
1  32.19000244  5717.399902       NaN          NaN  23.19000244         5719   
2  32.19000244  5739.055176       NaN          NaN  23.19000244         5733   
3  82.19000244  5742.049805       NaN          NaN  93.19000244         5734   
4  82.19000244  5721.529785       NaN          NaN  93.19000244         5720   
5          NaN          NaN       NaN          NaN          NaN          NaN   

  Label.3_x Unnamed: 7_y Label.4_x Unnamed: 9_y   ...    Label.9_x  \
1       NaN          NaN       NaN          NaN   ...          NaN   
2       NaN          NaN       NaN          NaN   ...          NaN   
3       NaN          NaN       NaN          NaN   ...          NaN   
4       NaN          NaN       NaN          NaN   ...          NaN   
5       NaN          NaN       NaN          NaN   ...          NaN   

  Unnamed: 19_y Label.10_x Left Levee_y Label.11_x Right Levee_y   Label.12_x  \
1           NaN        NaN          NaN        NaN           NaN            0   
2           NaN        NaN          NaN        NaN           NaN  23.19000053   
3           NaN        NaN          NaN        NaN           NaN   27.8566672   
4           NaN        NaN          NaN        NaN           NaN  32.52333387   
5           NaN        NaN          NaN        NaN           NaN  37.19000053   

   WS  CWCB-100yr_y Label.13_x Set WS_y  
1       5723.828125        NaN      NaN  
2        5728.10498        NaN      NaN  
3       5728.179688        NaN      NaN  
4       5728.253906        NaN      NaN  
5       5728.328613        NaN      NaN  

[5 rows x 28 columns]

## Plot q distribution

In [20]:
def q_histogram(values_list):
    """function to create interactive bokeh histogram plot. Inputs are a list of 
    values (which were generated in the perdentile definition), """
    p1 = figure(title="q distribution - Lower Fourmile",tools="save",
                background_fill_color="#E8DDCB", y_range = (0,80))

    mu = np.mean(values_list)
    sigma = np.std(values_list)
#     print(mu, sigma)

    hist, edges = np.histogram(values_list, density=False, bins='auto')
#     x = np.linspace(0, 9000, 1000)
#     pdf = 1/(sigma * np.sqrt(2*np.pi)) * np.exp(-(x-mu)**2 / (2*sigma**2))
#     cdf = (1+scipy.special.erf((x-mu)/np.sqrt(2*sigma**2)))/2

    p1.quad(top=hist, bottom=0, left=edges[:-1], right=edges[1:],
            fill_color=colors[2], line_color=colors[5], alpha=0.5, legend='q histogram')
#     p1.line(x, pdf, line_color="#D95B43", line_width=8, alpha=0.7, legend="PDF")
#     p1.line(x, cdf, line_color="white", line_width=2, alpha=0.7, legend="CDF")

    p1.legend.location = "center_right"
    p1.legend.background_fill_color = "darkgrey"
    p1.xaxis.axis_label = 'q - reach averaged cfs'
    p1.yaxis.axis_label = 'Pr(x)'
    
    # Add second axis and ws elevations
#     p1.extra_y_ranges = {"ws": Range1d(start=0, end=1)}
#     p1.add_layout(LinearAxis(y_range_name="ws", axis_label="ws_normalized"), 'right')
    
#     x2 = df.columns[10:510].values
#     for i in range(len(df)):
#         y2 = list(df.iloc[i,10:510])
#         y2 = [pd.to_numeric(i, errors='coerce') for i in y2]
#         y2_maxval = np.max(y2)
#         y2 = y2/y2_maxval
#         p1.circle(x2, y2, color='blue', y_range_name="ws_normalized", alpha=.01)
            
    output_notebook()
    # output_file('test.html')
    show(p1)

In [21]:
q_histogram(q_vals)

Loading BokehJS ...

## Define function for profile plot

In [80]:
# Define function for creating profile plot
def uncertainty_profile_plot(ws_dataframe, percentiles, median, title, x_axis_label, y_axis_label):
    alpha_val = 0.35
    alpha_val_outliers = 0.35
    
    # Find x,y range for plot dimensions (also for scaling y axis to reasonable sloping profile)
    df[df.columns[10]] = df[df.columns[10]].apply(pd.to_numeric)
    y_min = np.min(df[df.columns[10]]) - 5000
    y_max = np.max(df[df.columns[10]]) + 100
    
    # Define extents of profile's ground data
    x_minG = np.min(df_profile['Label.8_x'])
    x_maxG = np.max(df_profile['Label.8_x'])
    y_minG = np.min(df_profile['Ground_y'])
    
    # Create the figure: p
    p = figure(title=title, x_axis_label=x_axis_label, y_axis_label=y_axis_label, width=800, 
               y_range=(y_min, y_max), x_range=(x_minG, x_maxG))
    
    # Create water surface line plot
    for j in range(10,510):
        if ws_dataframe.columns[j] < percentiles[0]:
            p.line(ws_dataframe['XS'], ws_dataframe[ws_dataframe.columns[j]], alpha=alpha_val_outliers, color=colors[0], legend='0-100 percentile')
        elif percentiles[0] < ws_dataframe.columns[j] < percentiles[1]:
            p.line(ws_dataframe['XS'], ws_dataframe[ws_dataframe.columns[j]], alpha=alpha_val, color=colors[1], legend='10-90 percentile')
        elif percentiles[1] < ws_dataframe.columns[j] < percentiles[2]:
            p.line(ws_dataframe['XS'], ws_dataframe[ws_dataframe.columns[j]], alpha=alpha_val, color=colors[2], legend='25-75 percentile')
        elif percentiles[2] < ws_dataframe.columns[j] < percentiles[3]:
            p.line(df['XS'], ws_dataframe[ws_dataframe.columns[j]], alpha=alpha_val, color=colors[3])
        else:
            p.line(df['XS'], ws_dataframe[ws_dataframe.columns[j]], alpha=alpha_val_outliers, color=colors[4])


        # Plot the mode q value
        if ws_dataframe.columns[j] == median:
            p.line(ws_dataframe['XS'], ws_dataframe[ws_dataframe.columns[j]], color=colors[5], line_width=5, legend='median')


    # Create ground surface glyph plot
    p.line(df_profile['Label.8_x'], df_profile['Ground_y'], color='gray', line_width=3, legend='ground')
    
    p.legend.location = "center_right"
    
    # Add two additional x,y pairs to allow for path glyph to fill under ground rather than over
#     ground_x = [x_minG] + list(df_profile['Label.8_x']) + [x_maxG]
#     ground_y = [(y_min - 5)] + list(df_profile['Ground_y']) + [(y_min - 5)]
#     p.patch(ground_x, ground_y, color='lightgray', alpha=0.8)
    
    output_notebook()
    # output_file('test.html')
    show(p)

## Create profile plot

In [57]:
uncertainty_profile_plot(df, q_percentile_vals, q_median, 'q profile - Lower Fourmile', 'river_station - feet', 'Elevation - ft')

Loading BokehJS ...

## Import cross section ground data

In [12]:
# Import xs data from hec-ras' profile plot, copy values to clipboard option
df_xs = pd.read_csv('XS.csv', header=1)


df_xs_cols = df_xs.columns.values

for j in range(len(df_xs_cols)):
    label1 = df_xs[df_xs.columns[j]].iloc[0]
    label2 = df_xs_cols[j]
    label3 = label2 + '_' + label1

    # Append x,y labels to existing columns headers
    df_xs.rename(columns={label2:label3}, inplace=True)  

# Drop the first row now that its appended to the column headers
df_xs = df_xs.iloc[1:,:]

# Convert to numeric from string
df_xs[['Label.1_x', 'Ground_y']] = df_xs[['Label.1_x','Ground_y']].apply(pd.to_numeric)

df_xs.head()

Label_x Unnamed: 1_y  Label.1_x     Ground_y    Label.2_x   Bank Sta_y  \
1           99  6598.619141       0.00  6612.310059  137.7200012  6590.700195   
2           99         6610       1.98  6610.890137          NaN          NaN   
3          127         6610       2.96  6610.180176  159.7700043  6590.720215   
4          127  6594.631836       3.95  6609.470215          NaN          NaN   
5  126.8700027  6594.680176       4.94  6608.770020          NaN          NaN   

     Label.3_x WS CWCB-100yr_y  
1          127     6598.532715  
2  187.9481049     6598.532715  
3          NaN             NaN  
4  148.8000031     6598.532715  
5          NaN             NaN

## Define function for cross section plot

In [58]:
# Define function for creating cross section plot
def uncertainty_xs_plot(ws_dataframe, xs_dataframe, percentiles, median, title, x_axis_label, y_axis_label):
    alpha_val = 0.25
    alpha_val_outliers = 0.1
    
    # Create the figure: p
    p = figure(title=title, x_axis_label=x_axis_label, y_axis_label=y_axis_label, width=800)
    
    # Define extents of cross section's x values
    x_min = np.min(xs_dataframe['Label.1_x'])
    x_max = np.max(xs_dataframe['Label.1_x'])
    y_min = np.min(xs_dataframe['Ground_y'])

    # Create water surface line plots
    for j in range(10,510):
        # Define x,y pairs for xs water surfaces (flat water)
        x_vals = [x_min, x_max]
        y_vals = [ws_dataframe.iloc[0,j], ws_dataframe.iloc[0,j]]

        if ws_dataframe.columns[j] < percentiles[0]:
            p.line(x_vals, y_vals, alpha=alpha_val_outliers, color=colors[0], legend='0-100 percentile values')
            pass
        elif percentiles[0] < ws_dataframe.columns[j] < percentiles[1]:
            p.line(x_vals, y_vals, alpha=alpha_val_outliers, color=colors[1], legend='10-90 percentile values')
        elif percentiles[1] < ws_dataframe.columns[j] < percentiles[2]:
            p.line(x_vals, y_vals, alpha=alpha_val, color=colors[2], legend='25-75 percentile values')
        elif percentiles[2] < ws_dataframe.columns[j] < percentiles[3]:
            p.line(x_vals, y_vals, alpha=alpha_val_outliers, color=colors[3])
        else:
            p.line(x_vals, y_vals, alpha=alpha_val_outliers, color=colors[4])
            pass

        # Plot the mode q value
        if ws_dataframe.columns[j] == median:
            p.line(x_vals, y_vals, color=colors[5], line_width=5, legend='median value')

    # Create ground surface glyph plot
    p.line(xs_dataframe['Label.1_x'], xs_dataframe['Ground_y'], color='lightgray', line_width=3)
    
    # Add two additional x,y pairs to allow for path glyph to fill under ground rather than over
    ground_x = [x_min] + list(xs_dataframe['Label.1_x']) + [x_max]
    ground_y = [(y_min - 5)] + list(xs_dataframe['Ground_y']) + [(y_min - 5)] 
    p.patch(ground_x, ground_y, color='lightgray', alpha=0.8)
    
    # Create structure glyph plot
    p.patch(xs_dataframe['Label_x'] ,xs_dataframe['Unnamed: 1_y'], color='gray', alpha=0.8)
    p.line(xs_dataframe['Label_x'], xs_dataframe['Unnamed: 1_y'], color='gray', line_width=3, legend='ground')
    
    output_notebook()
    # output_file('test.html')
    show(p)

## q Cross Section Plot

In [60]:
uncertainty_xs_plot(df, df_xs, q_percentile_vals, q_median, 'q Cross Section - Lower Fourmile', 'XS 24750 station', 'Elevation')

Loading BokehJS ...

## Import mannning's n results

In [84]:
df_mannings = pd.read_csv('Mannings_n.csv', header=None)

i=0
# Append statistic columns and average discharges to column names
for j in range(0,510):
    df_mannings.rename(columns={j:df_mannings.iloc[i,j]}, inplace=True)

RESTART HERE, FIX REPETITIVE N VALUES, THEN TRY TO PRINT THE PROFILE PLOT WITH ALL  LINES SHOWING
# fix the repetive values in the n-values (must be unique for later indexing)
# def check_in_set(value, set):
#     """ for iteratively correcting repeated manning's values"""
#     in_set = False
#     if value in set:
#         in_set = True
#     else:
#         in_set = False
#     return in_set
        

mannings_set = set{}
# df_profile_cols = df_profile.columns.values

for j in range(10,510):
    in_set = True    
    if df_mannings.columns.values[j] in mannings_set:
        new_n = df_mannings.columns.values[j] + 0.000001
    
    
    label1 = df_profile[df_profile.columns[j]].iloc[0]
    label2 = df_profile_cols[j]
    label3 = label2 + '_' + label1

    # Append x,y labels to existing columns headers
    df_profile.rename(columns={label2:label3}, inplace=True) 
    
# df_mannings = df_mannings.iloc[1:,:]
df_mannings = df_mannings.drop([0,230])
df_mannings.head()

XS  DIFF      MAX     AVERAGE      MIN  STDEV   99th PCT  90thPCT  \
1  24915.69     0  6598.53     6598.53  6598.53      0    6598.53  6598.53   
2  24750.84  0.13  6588.92  6588.79038  6588.79  0.003    6588.79  6588.79   
3  24494.04     0  6578.16     6578.16  6578.16      0    6578.16  6578.16   
4  24361.28     0  6567.89     6567.89  6567.89      0    6567.89  6567.89   
5  24241.61  0.23  6560.03  6559.80306   6559.8  0.019  6559.8906   6559.8   

  10th PCT  1st PCT   ...       0.075    0.075    0.075    0.075    0.075  \
1  6598.53  6598.53   ...     6598.53  6598.53  6598.53  6598.53  6598.53   
2  6588.79  6588.79   ...     6588.79  6588.79  6588.79  6588.79  6588.79   
3  6578.16  6578.16   ...     6578.16  6578.16  6578.16  6578.16  6578.16   
4  6567.89  6567.89   ...     6567.89  6567.89  6567.89  6567.89  6567.89   
5   6559.8   6559.8   ...     6559.89  6559.89  6559.89  6559.89  6559.89   

     0.076    0.077    0.079    0.083    0.084  
1  6598.53  6598.53  6598.53  6598.53  6598.53  
2  6588.79  6588.79  6588.79  6588.85  6588.92  
3  6578.16  6578.16  6578.16  6578.16  6578.16  
4  6567.89  6567.89  6567.89  6567.89  6567.89  
5  6559.95  6559.99  6559.98  6560.02  6560.03  

[5 rows x 510 columns]

## Define percentiles - n

In [79]:
# Define the percentile ranges of interest
n_percentiles = [10,25,75,90]
n_vals = (df_mannings.columns.values[10:])
n_vals = pd.to_numeric(n_vals)#, coerce=True)
n_percentile_vals = np.percentile(n_vals, n_percentiles)
n_percentile_vals

# Find the median of the q values

# If dataset is even in length, drop the last entry to avoid averaging middle two values
if np.remainder(len(n_vals), 2) == 0:
    n_vals_even = n_vals[:-1]
    n_median = np.median(n_vals_even)
else:
    n_median = np.median(n_vals)

print ('median of n_vals: ', n_median, 'n_percentile_vals: ', n_percentile_vals)

median of n_vals:  0.049 n_percentile_vals:  [ 0.032  0.04   0.059  0.066]


In [86]:
# print (n_vals)

In [91]:
print(df_mannings[df_mannings.columns[200]])

       0.045    0.045    0.045    0.045    0.045    0.045    0.045    0.045  \
1    6598.53  6598.53  6598.53  6598.53  6598.53  6598.53  6598.53  6598.53   
2    6588.79  6588.79  6588.79  6588.79  6588.79  6588.79  6588.79  6588.79   
3    6578.16  6578.16  6578.16  6578.16  6578.16  6578.16  6578.16  6578.16   
4    6567.89  6567.89  6567.89  6567.89  6567.89  6567.89  6567.89  6567.89   
5    6559.80  6559.80  6559.80  6559.80  6559.80  6559.80  6559.80  6559.80   
6    6553.14  6553.14  6553.14  6553.14  6553.14  6553.14  6553.14  6553.14   
7    6546.83  6546.83  6546.83  6546.83  6546.83  6546.83  6546.83  6546.83   
8    6535.94  6535.94  6535.94  6535.94  6535.94  6535.94  6535.94  6535.94   
9    6526.57  6526.57  6526.57  6526.57  6526.57  6526.57  6526.57  6526.57   
10   6517.59  6517.59  6517.59  6517.59  6517.59  6517.59  6517.59  6517.59   
11   6507.82  6507.82  6507.82  6507.82  6507.82  6507.82  6507.82  6507.82   
12   6502.92  6502.92  6502.92  6502.92  6502.92  65

In [66]:
# y_min = np.min(df[df.columns[10]]) - 5000
# y_max = np.max(df[df.columns[10]]) + 100

# y_min
# y_max

# # Define extents of profile's ground data
# x_minG = np.min(df_profile['Label.8_x'])
# x_maxG = np.max(df_profile['Label.8_x'])
# y_minG = np.min(df_profile['Ground_y'])

print (x_minG, x_maxG, y_minG)

0.0 24894.31002 5717.399902


## n Value WS plots - profile 

In [82]:
uncertainty_profile_plot(df_mannings, n_percentile_vals, n_median, 'mannings n profile - Lower Fourmile', 'river_station - feet', 'Elevation - ft')


Loading BokehJS ...

## n value WS plot - cross section

## XS location WS plots - profile

## Combined factors WS plots

In [15]:
p2 = figure(title="q distribution",tools="save", background_fill_color="#E8DDCB", y_range = (0,1))

# print ('len df:',len(df))
# print ('len x2:',len(x2))
for i in range(len(df)):
    y2 = list(df.iloc[i,10:510])
#     print ('len y2:', len(y2))
    y2 = [pd.to_numeric(i, errors='coerce') for i in y2]
# 
    
    y2_norm1 = y2 / np.linalg.norm(y2)
    y3 = y2[:,np.newaxis]
    y2_norm2 = normalize(y3, axis=0).ravel()
    
#         y2 = np.asarray(y2, dtype=np.float)
#     y2_normalized = preprocessing.normalize(y2, norm='l2')
    
#     print ('len y2:', len(y2))
#     y2_maxval = np.max(y2)
#     for j in range(len(y2)):
#         print (y2[j], y2_maxval)
#         y2[j] = y2[j]/y2_maxval

# print(y2)
#     print ('len y2:', len(y2))
#     p2.circle(x2, y2, alpha=.01)
    
# output_notebook()
# # output_file('test.html')
# show(p2)

# x = np.random.rand(1000)*10
# norm1 = x / np.linalg.norm(x)
# norm2 = normalize(x[:,np.newaxis], axis=0).ravel()

TypeError: list indices must be integers or slices, not tuple

In [ ]:
# # print (df.columns[10:510].values)
# for i in range(len(df)):
#     y2 = list(df.iloc[i,10:510])
#     y2 = [pd.to_numeric(i, errors='coerce') for i in y2]
#     y2_maxval = np.max(y2)
#     y2 = y2/y2_max
# #     print(y2_maxval)
# #     y2 = y2/y2_maxval

In [ ]:
# References:
# Embedding Bokeh Server in Jupyter: http://biobits.org/bokeh-jupyter-embed.html
# https://github.com/ecerami/pydata-essentials/blob/master/bokeh/data/iris.data
# Bokeh histograms: 